### ChromaDB method - create vectorstore based on Chroma

In [ ]:
import chromadb
from llama_index.core import VectorStoreIndex, SimpleDirectoryReader
from llama_index.vector_stores.chroma.base import ChromaVectorStore
from llama_index.core import StorageContext
from llama_index.core import ServiceContext
from llama_index.core import Document

from llama_index.embeddings.huggingface.base import HuggingFaceEmbedding
from llama_index.core import Settings

import nest_asyncio
nest_asyncio.apply()

import time

In [ ]:
# load some documents
documents = SimpleDirectoryReader(input_files=[
                                    "../raw_documents/overview_background.txt",
                                    "../raw_documents/HI_Knowledge_Base.pdf",
                                    "../raw_documents/HI Chapter Summary Version 1.3.pdf",
                                    "../raw_documents/qna.txt"
                                  ]).load_data()
document = Document(text="\n\n".join([doc.text for doc in documents]))

In [ ]:
# initialize client, setting path to save data
db = chromadb.PersistentClient(path="../models/chroma_db")

In [ ]:
# create collection
chroma_collection = db.get_or_create_collection("quickstart")

In [ ]:
# assign chroma as the vector_store to the context
vector_store = ChromaVectorStore(chroma_collection=chroma_collection)

In [ ]:
Settings.llm = None
Settings.chunk_size = 1024
Settings.embed_model = "local:../models/fine-tuned-embeddings"

In [ ]:
nodes = Settings.node_parser.get_nodes_from_documents(documents)

In [ ]:
storage_context = StorageContext.from_defaults(vector_store=vector_store)

In [ ]:
storage_context.docstore.add_documents(nodes)

In [ ]:
start_time = time.time()

In [ ]:
vector_index = VectorStoreIndex(nodes, storage_context=storage_context)

In [ ]:
vector_query_engine = vector_index.as_query_engine()

In [ ]:
indexing_cost = time.time() - start_time
indexing_cost = indexing_cost / 60
print(f"Indexing time: {indexing_cost:.1f} mins")

In [ ]:
response = vector_query_engine.query("what is the healthcare philosophy in singapore")
response

### ChromaDB method - load vectorstore based on Chroma

In [ ]:
import chromadb
from llama_index.core import VectorStoreIndex, SimpleDirectoryReader
from llama_index.vector_stores.chroma.base import ChromaVectorStore
from llama_index.core import StorageContext
from llama_index.core import ServiceContext
from llama_index.core import Document
from llama_index.core import Settings

from llama_index.embeddings.huggingface.base import HuggingFaceEmbedding
from llama_index.llms.openai import OpenAI
from llama_index.core.memory import ChatMemoryBuffer

import time

In [ ]:
fine_tuned_path = "local:../models/fine-tuned-embeddings"

In [ ]:
llm = OpenAI(model="gpt-4-0125-preview", temperature=0.0)

In [ ]:
Settings.llm = llm
Settings.embed_model = fine_tuned_path

In [ ]:
db = chromadb.PersistentClient(path="../models/chroma_db")

In [ ]:
chroma_collection = db.get_or_create_collection("quickstart")

In [ ]:
# assign chroma as the vector_store to the context
vector_store = ChromaVectorStore(chroma_collection=chroma_collection)
storage_context = StorageContext.from_defaults(vector_store=vector_store)

In [ ]:
# create your index
index = VectorStoreIndex.from_vector_store(
    vector_store=vector_store,
    storage_context=storage_context
)

In [ ]:
system_content = ("You are a helpful study assistant. "
                  "You do not respond as 'User' or pretend to be 'User'. "
                  "You only respond once as 'Assistant'."
)

In [ ]:
memory = ChatMemoryBuffer.from_defaults(token_limit=15000)

In [ ]:
chat_engine = index.as_chat_engine(
    chat_mode="context",
    memory=memory,
    system_prompt=system_content
)

In [ ]:
prompt = """
Question: Which of the following is NOT a characteristic of medical expense insurance?
A. Pro ration factor and co-insurance.
B. Deductibles apply for all treatments.
C. Impose Sub- Limits.
D. Can be issued as a rider or stand-alone.
"""

In [ ]:
res = chat_engine.chat(prompt)
print(res.response)

In [ ]:
hi_engine = index.as_query_engine(
                memory=memory,
                system_prompt=system_content,
                similarity_top_k=10,
                streaming=True
)

In [ ]:
res = hi_engine.query(prompt)
print(res)